In [ ]:
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import numpy as np
import math
from matplotlib.animation import FFMpegWriter
import warnings
import copy
%matplotlib osx

In [ ]:
NX = 20 * 2
NY = 20 * 2

d = 5
dx = d
dy = d

ice_height = 500

Z = np.full((NX, NY), ice_height, dtype='float')

middle_start = NX // 2 - 5
middle_end = NX // 2 + 5
Z[:, middle_start:middle_end] = 0

# left
Z[:, 0] = 0
# right
Z[:, NY - 1] = 0
# front
Z[NX - 1, :] = 0
# back
Z[0, :] = 0

num_particles = 100
total_time = 50
dt = 1
g = -0.5

flow_side = np.zeros((NX, NY))
flow_front = np.zeros((NX, NY))

In [ ]:
metadata = dict(title='animation', artist='Nathaniel Mekis')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

X, Y = np.meshgrid(np.arange(NX), np.arange(NY))

surf = ax.plot_surface(X, Y, Z, color='white', alpha=0.5, shade=True, label='Ice')
surf_flow_side = ax.plot_surface(X, Y, flow_side, color='lightblue', alpha=1, shade=False, label='Flow')
surf_flow_front = ax.plot_surface(X, Y, flow_front, color='lightblue', alpha=1, shade=False)
 
particle_positions = np.zeros((num_particles, 2))

particle_positions = np.zeros((num_particles, 3))
particle_positions[:, 0] = np.random.uniform(middle_start, middle_end, num_particles)
particle_positions[:, 1] = np.random.uniform(0, NY - 1, num_particles)
particle_positions[:, 2] = ice_height + 1

particle_velocities = np.random.rand(num_particles, 3)
particle_velocities[:, 0:2] = np.random.uniform(-0.25, 0.25, (num_particles, 2))
particle_velocities[:, 2] = np.random.uniform(0.5, 1.5, num_particles)

particle_velocities[:, 0:2] *= 1
particle_velocities[:, 2] *= 4

ax.set_xlabel('Width (m)')
ax.set_ylabel('Length (m)')
ax.set_xlim(0, NX)
ax.set_ylim(0, NY)
ax.set_zlabel('Distance from Surface Ocean') 
ax.set_zlim(0, 1000)
ax.set_title("Eruption on Enceladus's Surface")
ax.grid(False)
ax.view_init(elev=5, azim=85)

flow_height = 0
time = 0

with writer.saving(fig, "animation5.mp4", dpi=200):
    while flow_height < ice_height:
        
        flow_side[:, middle_start:middle_end] = flow_height
        flow_front[0:NX - 1, middle_start:middle_end] = flow_height

        surf_flow_side.remove()
        surf_flow_front.remove()

        surf_flow_side = ax.plot_surface(X, Y, flow_side, color='lightblue', alpha=1, shade=False)
        surf_flow_front = ax.plot_surface(X, Y, flow_front, color='lightblue', alpha=1, shade=False)
        
        flow_height += 10

        plt.draw()
        plt.pause(0.000001)
        writer.grab_frame()
        
        if flow_height >= ice_height:
            scatter_particles = ax.scatter(particle_positions[:, 0], particle_positions[:, 1], particle_positions[:, 2], color='lightblue', marker='o')

    while time < total_time:
        
        for i in range(num_particles):
            if particle_positions[i, 2] <= 500:
                particle_velocities[i, :] = 0
        
        particle_positions[:, :2] += particle_velocities[:, :2] * dt
        particle_positions[:, 2] += particle_velocities[:, 2] * dt + 0.5 * g * dt**2
        particle_velocities[:, 2] += g * dt
        
        scatter_particles = ax.scatter(particle_positions[:, 0], particle_positions[:, 1], particle_positions[:, 2], color='lightblue', marker='o')

        time += dt
        
        plt.draw()
        plt.pause(0.000001)
        writer.grab_frame()   